In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 3).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [4]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO      MARCA       Date  \
2451  C202516   2025-11-03 2025-11-30       28  BOTICARIO 2025-11-03   

      NUM_CICLO ANO_CICLO CICLOMAIS2  dias_ate_inicio  match  
2451         16     C2025    C202519               59      1

In [5]:
ciclo_lanc = filtered_calendario['Ciclo'].max()

In [6]:
ciclo_lanc

'C202516'

In [7]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C16\arquivos para geração da sugestão\SIMILARES\PRODUTOS SIMILARES - BOT.xlsx")

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO', 'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [8]:
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].astype('str')

df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].replace(r'\.0$', '', regex=True)




In [9]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C16\arquivos para geração da sugestão\TABELA DE PEDIDO\Pedidos Semanais Especiais - BOT - 202516.xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [10]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv = df_pdv[~df_pdv['PDV'].isin([910173, 910291])]

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")
df_pdv_origi = df_pdv_origi[~df_pdv_origi['PDV'].isin([910173, 910291])]

In [11]:
df_pdv[df_pdv['PDV']==910291]

Empty DataFrame
Columns: [PDV, CANAL, DESCRIÇÃO, PDV DESC, REGIÃO, ESTADO, CIDADE, UF, MARCA, ANALISTA, GESTÃO, SUPERVISOR, STATUS]
Index: []

In [12]:


df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

df_pdv = df_pdv[df_pdv['STATUS'] != "INATIVO"]

df_pdv = df_pdv[df_pdv['STATUS'] != "MATRIZ"]

df_pdv = df_pdv[df_pdv['SUPERVISOR'] != 'Inativa']

df_pdv['MATCH'] = 1

In [13]:
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [14]:
import pyodbc
import configparser

#query de vendas por ciclo

config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = f'''
SELECT 
    B.PDV, 
    B.SKU,
    bd.SKU2, 
    COALESCE(bd.SKU2, b.SKU) AS SKU_FINAL,
    B.DESCRICAO,
    SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
    C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN base_depara bd on b.SKU = bd.SKU 
WHERE CAST(b.[DATA] AS DATE) >= DATEADD(YEAR, -1, GETDATE())
GROUP BY
    B.PDV, 
    B.SKU,
    bd.SKU2,
    B.DESCRICAO,
    C.Ciclo
HAVING SUM(CAST(b.VENDAS AS DECIMAL(18,2))) > 0
'''
dfi = pd.read_sql(query, conn)
conn.close()

dfi['SKU2'] = dfi['SKU2'].fillna("-")


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1001187263.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql(query, conn)


In [15]:

# 1. Agrupamento
df_agrupado = dfi.groupby(['PDV', 'SKU_FINAL', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU_FINAL', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_pivotadowawa = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_pivotadowawa.columns.name = None
df_pivotadowawa = df_pivotadowawa.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_pivotadowawa.head()

PDV  SKU_FINAL                             DESCRICAO  C202413  C202414  \
0  12522       1004         FLORATTA DES COL MY BLUE 75ml     15.0      2.0   
1  12522       1080  INTENSE GLOS LAB BUBBAL TUT/FRUT 5ml      0.0      4.0   
2  12522       1296   PMPCK THE BLEND DES ANTIT AER 2x75g      1.0      3.0   
3  12522       1302        PMPCK LILY DES ANTIT AER 2x75g      2.0      3.0   
4  12522       1314        PMPCK ZAAD DES ANTIT AER 2x75g      0.0      3.0   

   C202415  C202416  C202417  C202501  C202502  ...  C202504  C202505  \
0      3.0     56.0      6.0      1.0     11.0  ...      5.0     12.0   
1      0.0     10.0      2.0      2.0      1.0  ...      3.0      1.0   
2      3.0      2.0      0.0      0.0      0.0  ...      0.0      0.0   
3      5.0      6.0      0.0      0.0      0.0  ...      0.0      0.0   
4      1.0      1.0      0.0      0.0      0.0  ...      0.0      0.0   

   C202506  C202507  C202508  C202509  C202510  C202511  C202512  C202513  
0      7.0      2.0      0.0      1.0      2.0      5.0      3.0      0.0  
1      7.0     17.0      0.0      0.0      0.0      0.0      0.0      0.0  
2      0.0      0.0      0.0      0.0      0.0      0.0      0.0      2.0  
3      3.0      4.0      0.0      4.0      4.0      2.0      1.0      2.0  
4      0.0      0.0      0.0      0.0      0.0      1.0      1.0      0.0  

[5 rows x 21 columns]

In [16]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query_est_draft = f'''
select em.PDV ,
COALESCE(em.SKU_PARA , em.SKU) as SKU,
em.DESCRICAO,
d.salescurve as curva,
d.codcategory as categoria,
d.nextcycleprojection as proj_mar
,d.secondtonextcycleprojection as 'proj_mar+1',
em.[ESTOQUE ATUAL],em.[ESTOQUE EM TRANSITO],
em.[PEDIDO PENDENTE],
em.[DDV PREVISTO] ,
d.pricesellin as 'preço'
from estoque_mar em 
left join draft d on d.code = COALESCE(em.SKU_PARA , em.SKU) and d.loja_id = em.PDV 
where em.ORIGEM = 'BOT'
'''
df_draft_ = pd.read_sql(query_est_draft, conn)
conn.close()

#FALTA ATUALIZAR QUERY

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\268247862.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft_ = pd.read_sql(query_est_draft, conn)


In [17]:
df_draft = df_draft_

In [18]:
df_draft = df_draft[~df_draft['DESCRICAO'].str.contains('OUI', na=False)]

df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)

df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)

df_draft['PEDIDO PENDENTE'] = df_draft['PEDIDO PENDENTE'].astype(float)

df_draft.shape

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1474679865.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1474679865.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1474679865.py:7: SettingWithCopyWarning: 
A value is trying t

(356210, 12)

In [19]:
df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].fillna(0)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1952797845.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1952797845.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1952797845.py:5: SettingWithCopyWarning: 
A value is trying to be set 

In [20]:
df_draft = df_draft.groupby(['PDV','SKU','curva','categoria'])[['proj_mar','proj_mar+1','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DDV PREVISTO','preço']].max().reset_index()

In [21]:
df_draft['SKU'] = df_draft['SKU'].astype('Int64')

In [22]:
df_draft = pd.merge(df_draft,df_pivotadowawa,left_on=['PDV','SKU'],right_on=['PDV','SKU_FINAL'],how='inner')

In [23]:
df_draft.columns[13:31]

Index(['C202413', 'C202414', 'C202415', 'C202416', 'C202417', 'C202501',
       'C202502', 'C202503', 'C202504', 'C202505', 'C202506', 'C202507',
       'C202508', 'C202509', 'C202510', 'C202511', 'C202512', 'C202513'],
      dtype='object')

In [24]:
df_draft[df_draft['PDV']==24293]

Empty DataFrame
Columns: [PDV, SKU, curva, categoria, proj_mar, proj_mar+1, ESTOQUE ATUAL, ESTOQUE EM TRANSITO, PEDIDO PENDENTE, DDV PREVISTO, preço, SKU_FINAL, DESCRICAO, C202413, C202414, C202415, C202416, C202417, C202501, C202502, C202503, C202504, C202505, C202506, C202507, C202508, C202509, C202510, C202511, C202512, C202513]
Index: []

[0 rows x 31 columns]

In [25]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[13:31]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_31644\1731143361.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)


In [26]:
df_similares['PRODUTO SIMILAR'] = df_similares['PRODUTO SIMILAR'].astype('Int64')
df_similares['PRODUTO SIMILAR'].head()

0    57890
1    57890
2    57890
3    57890
4    57890
Name: PRODUTO SIMILAR, dtype: Int64

In [27]:
df_draft[['PDV', 'SKU']].dtypes

PDV    object
SKU     Int64
dtype: object

In [28]:
df_draft['PDV'] = df_draft['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [29]:
df_similares= df_similares[df_similares['PRODUTO SIMILAR'].notna()]

df_similares['PRODUTO SIMILAR'].value_counts()

PRODUTO SIMILAR
57211    154
48999    154
48997    154
57890     77
58987     77
48685     77
56530     77
57871     77
51869     77
49418     77
49943     77
49893     77
56402     77
56385     77
48780     77
58132     77
Name: count, dtype: Int64

In [30]:
df_final['SKU'].value_counts()

SKU
48997    154
48999    154
57211    140
49943    121
49893     91
57871     77
58987     77
56402     77
56385     77
57890     76
48780     75
51869     73
48685     72
49418     71
58132     66
56530     31
Name: count, dtype: Int64

In [31]:
#df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\arquivos para geração da sugestão\VENDAS_DIARIAS\FormFiltroConsultaVendaSintetica_17_06_2025_14_04_40.xls")
#df_venda_diaria.shape

In [32]:
df_venda_diaria = pd.read_csv(
    r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C15\arquivos para geração da sugestão\VENDAS_DIARIAS\vendas 20250815.csv",
    sep=';',
    dtype={'SKU_2': str},decimal=',')

In [33]:
df_venda_diaria['VENDAS_CICLO'] = df_venda_diaria['VENDAS_CICLO'].str.replace(r'\.', '', regex=True)

In [34]:
df_venda_diaria.head()

PDV     SKU                                 DESCRICAO VENDAS_CICLO  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml           11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK            1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4            5   
3   5699  47.950                          ZAAD EDP 95ml V6           12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml            2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [35]:
#df_venda_diaria['Ciclo'] = df_venda_diaria['Ciclo'].str.replace("C","C20") 

df_venda_diaria = df_venda_diaria.rename(columns={'VENDAS_CICLO':'Vendas_Total'})

df_venda_diaria.head()

PDV     SKU                                 DESCRICAO Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml           11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK            1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4            5   
3   5699  47.950                          ZAAD EDP 95ml V6           12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml            2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [36]:
df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].str.replace(',', '.', regex=False)

df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].astype('float')

df_venda_diaria['Vendas_Total'] = round(df_venda_diaria['Vendas_Total'],0)

df_venda_diaria['Vendas_Total'] = df_venda_diaria['Vendas_Total'].astype(str)

df_venda_diaria['Vendas_Total'] = (
    df_venda_diaria['Vendas_Total']
    .str.replace('.0', '', regex=False)
    .str.replace('.', '', regex=False)
    .astype('Int64')
)


df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml            11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK             1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4             5   
3   5699  47.950                          ZAAD EDP 95ml V6            12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml             2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [37]:
df_venda_diaria[(df_venda_diaria['PDV']==14668) & (df_venda_diaria['SKU']=='85096')]

Empty DataFrame
Columns: [PDV, SKU, DESCRICAO, Vendas_Total, Ciclo]
Index: []

In [38]:
df_venda_diaria2 = df_venda_diaria.pivot_table(
    index=["PDV", "SKU", "DESCRICAO"],
    columns="Ciclo",
    values="Vendas_Total",
    fill_value=0
).reset_index()

# Se quiser, reorganize as colunas colocando os ciclos ao final
df_venda_diaria.columns.name = None

df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  Vendas_Total  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml            11   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK             1   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4             5   
3   5699  47.950                          ZAAD EDP 95ml V6            12   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml             2   

     Ciclo  
0  C202307  
1  C202405  
2  C202409  
3  C202406  
4  C202416

In [39]:
df_venda_diaria.columns

Index(['PDV', 'SKU', 'DESCRICAO', 'Vendas_Total', 'Ciclo'], dtype='object')

In [40]:
df_venda_diaria

PDV     SKU                                 DESCRICAO  \
0        12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1        20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2        20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3         5699  47.950                          ZAAD EDP 95ml V6   
4        20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   
...        ...     ...                                       ...   
1663315  20996  83.039                 QUASAR DES COL RUSH 100ml   
1663316  20970  52.025           BOTI BABY SAB LIQ GLIC V2 400ml   
1663317  20996  93.069  LA PIEL D/COL SPR CP PER AMBR DOUR 200ml   
1663318  13427  51.279         MAKE B BAS LIQ C/ GLYC TX 140 30g   
1663319  21278  52.014    CJ FLAC OUI EDP ICONIQUE INTENSE 3x1ml   

         Vendas_Total    Ciclo  
0                  11  C202307  
1                   1  C202405  
2                   5  C202409  
3                  12  C202406  
4                   2  C202416  
...               ...      ...  
1663315             1  C202415  
1663316             6  C202511  
1663317            10  C202414  
1663318             1  C202309  
1663319             2  C202511  

[1663320 rows x 5 columns]

In [41]:
#df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

#df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

#df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

#df_venda_diaria = df_venda_diaria.drop(columns='Date')

#df_venda_diaria.shape

In [42]:
# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
#df_venda_diaria = df_venda_diaria.sort_values(by=['Unidade de Negócio', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
#df_venda_diaria['Quantidade Acumulada'] = (df_venda_diaria.groupby(['Unidade de Negócio', 'Código do Produto'])['Quantidade'].cumsum())  # acumulado por grupo até a data da linha

#df_venda_diaria.shape

In [43]:
#df_venda_diaria = df_venda_diaria.drop_duplicates()

#df_venda_agrupado = df_venda_diaria.fillna(0).groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade Acumulada'].max().reset_index()
#df_venda_agrupado

In [44]:
#df_venda_agrupado[(df_venda_agrupado['Ciclo']=='C202213')&(df_venda_agrupado['Código do Produto']==81054)&(df_venda_agrupado['PDV']=='20994')]

In [45]:
#df_venda_agrupado[['Ciclo','Código do Produto','PDV']].dtypes

In [46]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].dtypes

CICLO SIMILAR      object
PRODUTO SIMILAR     Int64
PDV                 int64
dtype: object

In [47]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

(1527, 60)

In [48]:
#df_final = df_final.drop(columns=['PDV DESC','status','SKU','Descrição','Lançamento','Item analisado','Planograma','Quantidade por caixa'])

In [49]:
df_final.head()

PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO  \
0               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
1               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
2               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
3               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
4               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   

   PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
1            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
2            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
3            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
4            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   

  FOCO  IAF            CATEGORIA MARCA % CONSUMIDOR  ... C202511 C202512  \
0  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...     2.0     0.0   
1  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...    24.0     1.0   
2  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...     7.0     1.0   
3  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...     1.0     1.0   
4  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...     0.0     2.0   

  C202513 CRESCIMENTO    Ciclo  INICIO CICLO  FIM CICLO DURAÇÃO match  \
0     0.0      0.0382  C202516    2025-11-03 2025-11-30      28     1   
1     0.0     -0.0456  C202516    2025-11-03 2025-11-30      28     1   
2     0.0      0.0433  C202516    2025-11-03 2025-11-30      28     1   
3     0.0     -0.0701  C202516    2025-11-03 2025-11-30      28     1   
4     0.0      0.0421  C202516    2025-11-03 2025-11-30      28     1   

  dias_ate_inicio  
0              59  
1              59  
2              59  
3              59  
4              59  

[5 rows x 60 columns]

In [50]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [51]:

df_venda_diaria = df_venda_diaria.rename(columns={'Vendas_Total':'Vendas Ciclo Lançamento'})
df_venda_diaria.head()

PDV     SKU                                 DESCRICAO  \
0  12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47.950                          ZAAD EDP 95ml V6   
4  20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [52]:
df_final['CICLO SIMILAR'] = df_final['CICLO SIMILAR'].fillna('0')
df_final['CICLO SIMILAR'] 

0        C202415
21       C202415
42       C202415
63       C202415
84       C202415
          ...   
25683          0
25684          0
25685          0
25686          0
25687          0
Name: CICLO SIMILAR, Length: 1527, dtype: object

In [53]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].head()

CICLO SIMILAR  PRODUTO SIMILAR    PDV
0        C202415            57890  12522
21       C202415            57890  12817
42       C202415            57890  12818
63       C202415            57890  12820
84       C202415            57890  12823

In [54]:


df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')



In [55]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'SKU', 'curva', 'categoria', 'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL',
       'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', 'DESCRICAO', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506', 'C202507', 'C202508', 'C202509', 'C202510', 'C202511',
       'C202512', 'C202513', 'CRESCIMENTO', 'Ciclo_x', 'INICIO CICLO_x',
       'FIM CICLO_x', 'DURAÇÃO_x', 'match', 'dias_ate_inicio', 'Ciclo_y',
       'INICIO CICLO_y', 'FIM CICLO_y', 'DURAÇÃO_y'],
      dtype='object')

In [56]:
df_final['PRODUTO SIMILAR']

0        57890
21       57890
42       57890
63       57890
84       57890
         ...  
25683    58132
25684    58132
25685    58132
25686    58132
25687    58132
Name: PRODUTO SIMILAR, Length: 1527, dtype: Int64

In [57]:
df_venda_diaria

PDV     SKU                                 DESCRICAO  \
0        12522  51.944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1        20998  77.557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2        20858  74.103            GLAMOUR DES COL SEC BL 75ml V4   
3         5699  47.950                          ZAAD EDP 95ml V6   
4        20993  50.297               ESTJ DEM LILY ESSENCE 4x4ml   
...        ...     ...                                       ...   
1663315  20996  83.039                 QUASAR DES COL RUSH 100ml   
1663316  20970  52.025           BOTI BABY SAB LIQ GLIC V2 400ml   
1663317  20996  93.069  LA PIEL D/COL SPR CP PER AMBR DOUR 200ml   
1663318  13427  51.279         MAKE B BAS LIQ C/ GLYC TX 140 30g   
1663319  21278  52.014    CJ FLAC OUI EDP ICONIQUE INTENSE 3x1ml   

         Vendas Ciclo Lançamento    Ciclo  
0                             11  C202307  
1                              1  C202405  
2                              5  C202409  
3                             12  C202406  
4                              2  C202416  
...                          ...      ...  
1663315                        1  C202415  
1663316                        6  C202511  
1663317                       10  C202414  
1663318                        1  C202309  
1663319                        2  C202511  

[1663320 rows x 5 columns]

In [58]:
df_venda_diaria['SKU'] = df_venda_diaria['SKU'].astype('str')

df_venda_diaria['SKU'] = df_venda_diaria['SKU'].str.replace('.','')

df_venda_diaria.head()

PDV    SKU                                 DESCRICAO  \
0  12522  51944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47950                          ZAAD EDP 95ml V6   
4  20993  50297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [59]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('str')

In [60]:
df_final.head()

PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO  \
0                89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
21               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
42               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
63               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
84               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   

   PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
21           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
42           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
63           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
84           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   

   FOCO  IAF            CATEGORIA MARCA % CONSUMIDOR  ...  Ciclo_x  \
0   Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...  C202516   
21  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...  C202516   
42  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...  C202516   
63  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...  C202516   
84  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...  C202516   

   INICIO CICLO_x FIM CICLO_x DURAÇÃO_x  match  dias_ate_inicio  Ciclo_y  \
0      2025-11-03  2025-11-30        28      1               59  C202415   
21     2025-11-03  2025-11-30        28      1               59  C202415   
42     2025-11-03  2025-11-30        28      1               59  C202415   
63     2025-11-03  2025-11-30        28      1               59  C202415   
84     2025-11-03  2025-11-30        28      1               59  C202415   

   INICIO CICLO_y FIM CICLO_y DURAÇÃO_y  
0      2024-10-14  2024-11-03      21.0  
21     2024-10-14  2024-11-03      21.0  
42     2024-10-14  2024-11-03      21.0  
63     2024-10-14  2024-11-03      21.0  
84     2024-10-14  2024-11-03      21.0  

[5 rows x 64 columns]

In [61]:
df_final = pd.merge(left=df_final, right = df_venda_diaria[['PDV','SKU','Ciclo','Vendas Ciclo Lançamento']], right_on=['Ciclo','SKU','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [62]:
df_final.head()

PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO  \
0               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
1               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
2               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
3               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
4               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   

  PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
1           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
2           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
3           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
4           57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   

  FOCO  IAF            CATEGORIA MARCA % CONSUMIDOR  ... DURAÇÃO_x match  \
0  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
1  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
2  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
3  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
4  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   

  dias_ate_inicio  Ciclo_y  INICIO CICLO_y  FIM CICLO_y DURAÇÃO_y  SKU_y  \
0              59  C202415      2024-10-14   2024-11-03      21.0  57890   
1              59  C202415      2024-10-14   2024-11-03      21.0    NaN   
2              59  C202415      2024-10-14   2024-11-03      21.0    NaN   
3              59  C202415      2024-10-14   2024-11-03      21.0  57890   
4              59  C202415      2024-10-14   2024-11-03      21.0    NaN   

     Ciclo Vendas Ciclo Lançamento  
0  C202415                       1  
1      NaN                    <NA>  
2      NaN                    <NA>  
3  C202415                       2  
4      NaN                    <NA>  

[5 rows x 67 columns]

In [63]:
df_final.to_excel(r'C:\Users\joao.herculano\Documents\teste.xlsx',index=False)

In [64]:
df_final = df_final[df_final['PRODUTO LANÇAMENTO'].notna()]
df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)


In [65]:
df_final['PDV'].value_counts().min()

np.int64(19)

In [66]:
df_final.columns[29:46]

Index(['ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço',
       'SKU_FINAL', 'DESCRICAO', 'C202413', 'C202414', 'C202415', 'C202416',
       'C202417', 'C202501', 'C202502', 'C202503', 'C202504', 'C202505',
       'C202506'],
      dtype='object')

In [67]:
df_jacobina = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\REGIÃO JACOBINA\draft unificado.xlsx")

In [68]:
df_jacobina = df_jacobina[['PDV', 'SKU','202408', '202409',
       '202410', '202411', '202412', '202413', '202414', '202415', '202416',
       '202417', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507']]

In [69]:
ciclos = [
    '202408', '202409', '202410', '202411', '202412', '202413',
    '202414', '202415', '202416', '202417', '202501', '202502',
    '202503', '202504', '202505', '202506', '202507']

df_jacobina[ciclos] = df_jacobina[ciclos].fillna(0)

In [70]:
df_jacobina.head()

PDV    SKU  202408  202409  202410  202411  202412  202413  202414  \
0  24269  49014       1       0       5       1       1       1       2   
1  24268  49014       1       0       4       4       2       5       1   
2  24269  49016      36       3       1       1       1       0      14   
3  24268  49016      12       3       1       2       2       2       0   
4  24269  48141      32       2       3      95       3       2      41   

   202415  202416  202417  202501  202502  202503  202504  202505  202506  \
0       2       1       1       3       0       4       0       2       1   
1       3       4       4       3       0       2       4       2       0   
2       2       2       1       1      19       1       2       2      10   
3       0       3      11       4       3       0       4       2       1   
4       3       3       1       1       1       0      67       4      10   

   202507  
0       0  
1       1  
2       0  
3       0  
4       2

In [71]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

df_final.head()

PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO  \
0               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
1               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
2               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
3               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
4               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   

   PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
1            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
2            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
3            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
4            57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   

  FOCO  IAF            CATEGORIA MARCA % CONSUMIDOR  ... DURAÇÃO_x match  \
0  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
1  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
2  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
3  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   
4  Não  Não  CUIDADOS COM A PELE  LILY        15.01  ...        28     1   

  dias_ate_inicio  Ciclo_y  INICIO CICLO_y  FIM CICLO_y DURAÇÃO_y  SKU_y  \
0              59  C202415      2024-10-14   2024-11-03      21.0  57890   
1              59  C202415      2024-10-14   2024-11-03      21.0    NaN   
2              59  C202415      2024-10-14   2024-11-03      21.0    NaN   
3              59  C202415      2024-10-14   2024-11-03      21.0  57890   
4              59  C202415      2024-10-14   2024-11-03      21.0    NaN   

     Ciclo Vendas Ciclo Lançamento  
0  C202415                       1  
1      NaN                       0  
2      NaN                       0  
3  C202415                       2  
4      NaN                       0  

[5 rows x 67 columns]

In [72]:
df_final = pd.merge(left=df_final,right=df_jacobina,left_on=['PRODUTO SIMILAR','PDV'],right_on=['SKU','PDV'],how='left')

In [73]:
# Gera pares de colunas: coluna estática ↔ coluna de histórico
pares_validos = [
    (ciclo, f'Histórico de Vendas do Ciclo {ciclo}')
    for ciclo in ciclos
    if ciclo in df_final.columns and f'Histórico de Vendas do Ciclo {ciclo}' in df_final.columns
]

# Separa os nomes das colunas
colunas_estaticas = [c[0] for c in pares_validos]
colunas_historico = [c[1] for c in pares_validos]

# Aplica a regra: se valor na coluna estática for maior, sobrescreve no histórico
for col_estatica, col_hist in zip(colunas_estaticas, colunas_historico):
    df_final[col_hist] = df_final[col_estatica].where(
        df_final[col_estatica] > df_final[col_hist],
        df_final[col_hist]
    )


In [74]:
df_final

PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO  \
0                  89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
1                  89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
2                  89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
3                  89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
4                  89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g   
...                  ...                                       ...   
1522               58132          CUIDE-SE BEM DELEITE CHOCOLATUDO   
1523               58132          CUIDE-SE BEM DELEITE CHOCOLATUDO   
1524               58132          CUIDE-SE BEM DELEITE CHOCOLATUDO   
1525               58132          CUIDE-SE BEM DELEITE CHOCOLATUDO   
1526               58132          CUIDE-SE BEM DELEITE CHOCOLATUDO   

      PRODUTO SIMILAR                         DESCRIÇÃO SIMILAR CICLO SIMILAR  \
0               57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
1               57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
2               57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
3               57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
4               57890  LILY CREM ACET DES HID CPO GARDENIA 250g       C202415   
...               ...                                       ...           ...   
1522            58132          CUIDE-SE BEM DELEITE CHOCOLATUDO             0   
1523            58132          CUIDE-SE BEM DELEITE CHOCOLATUDO             0   
1524            58132          CUIDE-SE BEM DELEITE CHOCOLATUDO             0   
1525            58132          CUIDE-SE BEM DELEITE CHOCOLATUDO             0   
1526            58132          CUIDE-SE BEM DELEITE CHOCOLATUDO             0   

     FOCO  IAF            CATEGORIA         MARCA % CONSUMIDOR  ... 202415  \
0     Não  Não  CUIDADOS COM A PELE          LILY        15.01  ...    NaN   
1     Não  Não  CUIDADOS COM A PELE          LILY        15.01  ...    NaN   
2     Não  Não  CUIDADOS COM A PELE          LILY        15.01  ...    NaN   
3     Não  Não  CUIDADOS COM A PELE          LILY        15.01  ...    NaN   
4     Não  Não  CUIDADOS COM A PELE          LILY        15.01  ...    NaN   
...   ...  ...                  ...           ...          ...  ...    ...   
1522  Não  Não           PERFUMARIA  CUIDE-SE BEM            -  ...    NaN   
1523  Não  Não           PERFUMARIA  CUIDE-SE BEM            -  ...    0.0   
1524  Não  Não           PERFUMARIA  CUIDE-SE BEM            -  ...    0.0   
1525  Não  Não           PERFUMARIA  CUIDE-SE BEM            -  ...    NaN   
1526  Não  Não           PERFUMARIA  CUIDE-SE BEM            -  ...    NaN   

     202416 202417 202501  202502  202503 202504 202505 202506 202507  
0       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
1       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
2       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
3       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
4       NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
...     ...    ...    ...     ...     ...    ...    ...    ...    ...  
1522    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
1523    0.0   24.0    0.0     0.0     0.0    0.0    0.0    0.0    0.0  
1524    0.0   89.0    0.0     0.0     0.0    0.0    0.0    0.0    0.0  
1525    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  
1526    NaN    NaN    NaN     NaN     NaN    NaN    NaN    NaN    NaN  

[1527 rows x 85 columns]

In [75]:
df_final = df_final.fillna(0)

In [76]:
df_final.columns[35:53]

Index(['C202413', 'C202414', 'C202415', 'C202416', 'C202417', 'C202501',
       'C202502', 'C202503', 'C202504', 'C202505', 'C202506', 'C202507',
       'C202508', 'C202509', 'C202510', 'C202511', 'C202512', 'C202513'],
      dtype='object')

In [77]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[35:53]
# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

CRESCIMENTO = 0.2 if CRESCIMENTO < 0.2 else CRESCIMENTO

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


0.2

In [78]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [79]:
df_final.columns[46:53]

Index(['C202507', 'C202508', 'C202509', 'C202510', 'C202511', 'C202512',
       'C202513'],
      dtype='object')

In [80]:
VENDA_SIMILAR_6_MESES= df_final.columns[46:53]
df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final['Pico Vendas Similar Ultimos 6 ciclos'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].median(axis=1, skipna=True)




In [81]:
df_final[colunas_mensais].median(axis=1, skipna=True)


0       1.5
1       3.5
2       1.0
3       1.0
4       1.0
       ... 
1522    0.0
1523    0.0
1524    0.0
1525    0.0
1526    0.0
Length: 1527, dtype: float64

In [82]:
medi = df_final.groupby(['CANAL','UF','PRODUTO LANÇAMENTO'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})
medi

CANAL  UF  PRODUTO LANÇAMENTO  med_por_canal
0      CD  AL               48780            3.5
1      CD  AL               49154           29.0
2      CD  AL               49193           19.5
3      CD  AL               49893            0.0
4      CD  AL               49943            0.0
..    ...  ..                 ...            ...
242    VD  SE               88301            2.0
243    VD  SE               88730            0.0
244    VD  SE               88889            0.0
245    VD  SE               88911            5.5
246    VD  SE               89446            4.5

[247 rows x 4 columns]

In [83]:
#df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF'],how='inner')


In [84]:
df_final['TIPO DE PRODUTO']

0       EDICAO LIMITADA
1       EDICAO LIMITADA
2       EDICAO LIMITADA
3       EDICAO LIMITADA
4       EDICAO LIMITADA
             ...       
1522            REGULAR
1523            REGULAR
1524            REGULAR
1525            REGULAR
1526            REGULAR
Name: TIPO DE PRODUTO, Length: 1527, dtype: object

In [85]:
df_venda_diaria.head()

PDV    SKU                                 DESCRICAO  \
0  12522  51944     COFFEE DES COL MAN SEDUC TCH PRM 10ml   
1  20998  77557  QDB BASE LIQ SUPERMAT COR 06 Q 30ml RPCK   
2  20858  74103            GLAMOUR DES COL SEC BL 75ml V4   
3   5699  47950                          ZAAD EDP 95ml V6   
4  20993  50297               ESTJ DEM LILY ESSENCE 4x4ml   

   Vendas Ciclo Lançamento    Ciclo  
0                       11  C202307  
1                        1  C202405  
2                        5  C202409  
3                       12  C202406  
4                        2  C202416

In [86]:
df_dourado = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\DADOS DOURADO\VENDA\compilado de vendas.xlsx")

df_dourado['Data de venda'] = pd.to_datetime(df_dourado['Data de venda'], dayfirst=True)

df_dourado['de para pdv'] = df_dourado['de para pdv'].astype(str)

df_dourado['de para pdv'] = df_dourado['de para pdv'].str.replace(r'\.0$', '', regex=True)

# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'SKU', 'Ciclo'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_dourado['Quantidade Acumulada dourado'] = (
    df_dourado
    .groupby(['de para pdv', 'sku'])['Quantidade Vendida']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_dourado = pd.merge(left=df_dourado,right=calendario[['Date','Ciclo']],left_on='Data de venda',right_on='Date',how='inner')



df_dourado_agrupado = df_dourado.groupby(['de para pdv','sku','Ciclo'])['Quantidade Acumulada dourado'].max().reset_index()

df_dourado_agrupado = df_dourado_agrupado.rename(columns={'Ciclo':'Ciclo dourado'})



In [87]:
df_final['PDV'] = df_final['PDV'].astype(str)
df_final['PDV'].head()

0    12522
1    12817
2    12818
3    12820
4    12823
Name: PDV, dtype: object

In [88]:
df_final = pd.merge(left=df_final, right = df_dourado_agrupado, right_on=['Ciclo dourado','sku','de para pdv'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada dourado'] = df_final['Quantidade Acumulada dourado'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada dourado'] > 0, df_final['Quantidade Acumulada dourado'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada dourado')


df_final = df_final.drop(columns='Ciclo dourado')

In [89]:
df_depara_vdc = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\Filiais - Vitoria da Conquista 4.xlsx")

df_depara_vdc.head()

CP VIVA BEM  Protheus  PDVDEPARA.Practico        Canal  \
0         3559   70101.0             23713.0  MATRIZ - LJ   
1         7292   70103.0             23712.0         LOJA   
2         8708   70102.0             23711.0           VD   
3         8931       NaN             23710.0          NaN   
4        11191   70108.0             23709.0         LOJA   

                                            Endereço                CNPJ  \
0  Rua Zeferino Correia, nº 17, Centro, CEP 45.00...  14.378.160/0001-83   
1  Al. Rio Branco, nº 373, Centro, Cândido Sales ...  14.378.160/0006-98   
2  Al. Lima Guerra, nº 04, Centro, Vitória da Con...  14.378.160/0005-07   
3  Avenida Rosa Cruz, nº 80, Hiper B Preço Loja B...  14.378.160/0008-50   
4  Av. Juracy Magalhães, nº 3340, Shopping Conqui...  14.378.160/0009-30   

         CNPJ Locação  
0  14.378.160/0001-83  
1  14.378.160/0006-98  
2  14.378.160/0001-83  
3  14.378.160/0008-50  
4  14.378.160/0001-83

In [90]:
r'''df_vdc = pd.read_parquet(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\VENDAS VITORIA DA CONQUISTA\concatenado.parquet")

df_vdc['PDV'] = df_vdc['Quebra'].str.split(" -").str[0]

df_vdc['PDV'] = df_vdc['PDV'].astype('int64')

df_vdc = df_vdc.rename(columns={'Quebra2':'DATA VENDA'})

df_vdc['DATA VENDA'] = pd.to_datetime(df_vdc['DATA VENDA'], format='%d/%m/%Y')'''

'df_vdc = pd.read_parquet(r"C:\\Users\\joao.herculano\\GRUPO GINSENG\\Assistência Suprimentos - 2025\\SUPRIMENTOS\\Vitoria da Conquista\\HISTORICO VENDAS VITORIA DA CONQUISTA\\VENDAS VITORIA DA CONQUISTA\\concatenado.parquet")\n\ndf_vdc[\'PDV\'] = df_vdc[\'Quebra\'].str.split(" -").str[0]\n\ndf_vdc[\'PDV\'] = df_vdc[\'PDV\'].astype(\'int64\')\n\ndf_vdc = df_vdc.rename(columns={\'Quebra2\':\'DATA VENDA\'})\n\ndf_vdc[\'DATA VENDA\'] = pd.to_datetime(df_vdc[\'DATA VENDA\'], format=\'%d/%m/%Y\')'

In [91]:
'''df_vdc = pd.merge(df_vdc,df_depara_vdc[['CP VIVA BEM','PDVDEPARA.Practico']],left_on='PDV',right_on='CP VIVA BEM',how='inner')

df_vdc['Quantidade'] = df_vdc['Quantidade'].str.replace(r',000$','',regex=True)

df_vdc['Quantidade'] = df_vdc['Quantidade'].astype('Int64') '''

"df_vdc = pd.merge(df_vdc,df_depara_vdc[['CP VIVA BEM','PDVDEPARA.Practico']],left_on='PDV',right_on='CP VIVA BEM',how='inner')\n\ndf_vdc['Quantidade'] = df_vdc['Quantidade'].str.replace(r',000$','',regex=True)\n\ndf_vdc['Quantidade'] = df_vdc['Quantidade'].astype('Int64') "

In [92]:




# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
#df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'SKU', 'Ciclo'])

# Calcula a quantidade acumulada até o dia para cada grupo
r'''df_vdc['Quantidade Acumulada vdc'] = (
    df_vdc
    .groupby(['PDVDEPARA.Practico', 'Código'])['Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha'''

"df_vdc['Quantidade Acumulada vdc'] = (\n    df_vdc\n    .groupby(['PDVDEPARA.Practico', 'Código'])['Quantidade']\n    .cumsum()\n)  # acumulado por grupo até a data da linha"

In [93]:
r'''df_vdc = pd.merge(left=df_vdc,right=calendario[['Date','Ciclo']],left_on='DATA VENDA',right_on='Date',how='inner')

df_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',	'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()

df_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})


df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype(str).str.replace(r'\.0$', '', regex=True)
df_vdc_agrupado.head()'''



"df_vdc = pd.merge(left=df_vdc,right=calendario[['Date','Ciclo']],left_on='DATA VENDA',right_on='Date',how='inner')\n\ndf_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',\t'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()\n\ndf_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})\n\n\ndf_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype(str).str.replace(r'\\.0$', '', regex=True)\ndf_vdc_agrupado.head()"

In [94]:
r'''df_vdc_agrupado = df_vdc_agrupado.astype(str)

df_vdc_agrupado = df_vdc_agrupado.replace()'''

'df_vdc_agrupado = df_vdc_agrupado.astype(str)\n\ndf_vdc_agrupado = df_vdc_agrupado.replace()'

In [95]:
#df_vdc.to_excel(r"C:\Users\joao.herculano\Documents\df_vdc.xlsx",index=False)

In [96]:
r'''df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype(str)

df_vdc_agrupado['PDVDEPARA.Practico'].head()'''

"df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype(str)\n\ndf_vdc_agrupado['PDVDEPARA.Practico'].head()"

In [97]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

In [98]:
#df_vdc_agrupado['Código'] = df_vdc_agrupado['Código'].astype('Int64')

In [99]:
r'''df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada vdc'] = pd.to_numeric(
    df_final['Quantidade Acumulada vdc'],
    errors='coerce'  # valores inválidos viram NaN
).fillna(0).astype('Int64')


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc'] > 0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada vdc')


df_final = df_final.drop(columns='Ciclo vdc')'''



"df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')\n\ndf_final['Quantidade Acumulada vdc'] = pd.to_numeric(\n    df_final['Quantidade Acumulada vdc'],\n    errors='coerce'  # valores inválidos viram NaN\n).fillna(0).astype('Int64')\n\n\ndf_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc'] > 0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])\n\ndf_final = df_final.drop(columns='Quantidade Acumulada vdc')\n\n\ndf_final = df_final.drop(columns='Ciclo vdc')"

In [100]:

# Cálculo do crescimento
crescimento_final = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']
crescimento_final = crescimento_final.clip(lower=0.2, upper=0.8)  # limita entre 0 e 0.8
df_final['CRESCIMENTO_FINAL'] = crescimento_final

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_FINAL'].isna(),df_final['CRESCIMENTO_GERAL'],df_final['CRESCIMENTO_FINAL'])

df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_FINAL'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)

# Corrige mediana do histórico onde for zero
df_final['MEDIANA DO HISTÓRICO'] = np.where(
    df_final['MEDIANA DO HISTÓRICO'] == 0,
    0,
    df_final['MEDIANA DO HISTÓRICO']
)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)



# Cálculo do PV GINSENG
pv_crescimento = (df_final['CRESCIMENTO_FINAL']+1) * df_final['Vendas Ciclo Lançamento']
pv_mediana = (df_final['CRESCIMENTO_FINAL'] + 1) * df_final['MEDIANA DO HISTÓRICO']

df_final['PV GINSENG'] = np.where(
    pv_crescimento < df_final['MEDIANA DO HISTÓRICO'],
    pv_mediana.round(0),
    pv_crescimento.round(0)
)

# Se PV GINSENG for NA, substitui pela média por canal
df_final['PV GINSENG'] = df_final['PV GINSENG'].fillna(0)

df_final['PV GINSENG'] = df_final['PV GINSENG'].round(0).astype(int)

df_final.shape


(1527, 91)

In [101]:
#df_final.to_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\validação.xlsx",index=False)

In [102]:
print(df_final.columns[68:85])

Index(['202409', '202410', '202411', '202412', '202413', '202414', '202415',
       '202416', '202417', '202501', '202502', '202503', '202504', '202505',
       '202506', '202507', 'CRESCIMENTO_GERAL'],
      dtype='object')


In [103]:
import re

# identificar colunas de ciclo puro (ex: '202407')
colunas_ciclo_puro = [col for col in df_final.columns[68:85]]

for col in colunas_ciclo_puro:
    col_hist = f'C{col}'
    if col_hist in df_final.columns:
        # mantém o maior valor entre a coluna histórica e a pura
        df_final[col_hist] = df_final[[col_hist, col]].max(axis=1)

# remove as colunas puras
if colunas_ciclo_puro:
    df_final.drop(columns=colunas_ciclo_puro, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'SKU_x', 'curva', 'categoria', 'proj_mar', 'proj_mar+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C202509',
       'C202510', 'C202511', 'C202512', 'C202513', 'CRESCIMENTO', 'Ciclo',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'match', 'dias_ate_inicio',
       'INICIO CICLO SIMILAR', 'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR',
       'SKU_y', 'Ciclo', 'Vendas Ciclo Lançame

In [104]:
r'''print(df_final.columns[30:43])

df_final.drop(columns=df_final.columns[30:43],inplace=True)'''

'print(df_final.columns[30:43])\n\ndf_final.drop(columns=df_final.columns[30:43],inplace=True)'

In [105]:
df_final.columns[52]

'C202513'

In [106]:
df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

In [107]:
df_final = df_final.rename(columns={df_final.columns[48]: "C-4", df_final.columns[49]: "C-3",df_final.columns[50]: "C-2",df_final.columns[51]: "C-1",df_final.columns[52]:'VENDAS CICLO ATUAL'})


In [108]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='_Y').columns, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR', 'STATUS',
       'SKU_X', 'CURVA', 'CATEGORIA', 'PROJ_MAR', 'PROJ_MAR+1',
       'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO', 'PEDIDO PENDENTE',
       'DDV PREVISTO', 'PREÇO', 'SKU_FINAL', 'DESCRICAO', 'C202413', 'C202414',
       'C202415', 'C202416', 'C202417', 'C202501', 'C202502', 'C202503',
       'C202504', 'C202505', 'C202506', 'C202507', 'C202508', 'C-4', 'C-3',
       'C-2', 'C-1', 'VENDAS CICLO ATUAL', 'CRESCIMENTO', 'CICLO',
       'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'MATCH', 'DIAS_ATE_INICIO',
       'INICIO CICLO SIMILAR', 'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR',
       'CICLO', 'VENDAS CICLO LANÇAMENTO', 'SKU', '

In [109]:
df_final = df_final.rename(columns={'MARCA_X':'MARCA'})

In [110]:
df_final.shape

(1527, 73)

In [111]:
df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']] = df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']].fillna(0)

In [112]:
df_final = df_final.loc[:, ~df_final.columns.duplicated()]

colunas_desejadas = [
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    '% CONSUMIDOR',
    'MECANICA CONSUMIDOR',
    '% REVENDEDOR',
    'MECANICA REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'
]

df_final = df_final.reindex(columns=colunas_desejadas)

colunas_filtradas = [col for col in colunas_desejadas if col in df_final.columns]
df_final = df_final[colunas_filtradas]


In [113]:
'''df_final = df_final.reindex(columns=[
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'])
'''

"df_final = df_final.reindex(columns=[\n    'SUPERVISOR',\n    'ANALISTA',\n    'CANAL',\n    'UF',\n    'PDV',\n    'DESCRIÇÃO PDV',\n    'PRODUTO LANÇAMENTO',\n    'DESCRIÇÃO DO LANÇAMENTO',\n    'MARCA',\n    'CATEGORIA',\n    'MECANICA CONSUMIDOR',\n    '% CONSUMIDOR',\n    'MECANICA REVENDEDOR',\n    '% REVENDEDOR',\n    'TIPO DE PRODUTO',\n    'IAF',\n    'FOCO',\n    'PRODUTO SIMILAR',\n    'DESCRIÇÃO SIMILAR',\n    'CICLO SIMILAR',\n    'VENDAS CICLO LANÇAMENTO',\n    'C-4',\n    'C-3',\n    'C-2',\n    'C-1',\n    'VENDAS CICLO ATUAL',\n    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',\n    'PV GINSENG'])\n"

In [114]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [115]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype(str)

df_pdv_origi['PDV'].head()

df_pdv_origi = df_pdv_origi.rename(columns={'UF':'UF_CERTO'})

In [116]:
df_final= pd.merge(df_final,df_pdv_origi[['UF_CERTO','PDV']],on='PDV',how='inner')

In [117]:
df_final.columns

Index(['SUPERVISOR', 'ANALISTA', 'CANAL', 'UF', 'PDV', 'DESCRIÇÃO PDV',
       'PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'MARCA', 'CATEGORIA',
       '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'IAF', 'FOCO',
       'PRODUTO SIMILAR', 'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR',
       'VENDAS CICLO LANÇAMENTO', 'C-4', 'C-3', 'C-2', 'C-1',
       'VENDAS CICLO ATUAL', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
       'PV GINSENG', 'SUGESTÃO METASELLIN', 'SUGESTÃO ABASTECIMENTO',
       'SUGESTÃO COMERCIAL', 'UF_CERTO'],
      dtype='object')

In [118]:
df_final['UF']= df_final['UF_CERTO']

df_final = df_final.drop(columns=['UF_CERTO'])

df_final.head()

SUPERVISOR   ANALISTA CANAL  UF    PDV    DESCRIÇÃO PDV  \
0  Efigênia Herculano       LUAN    LJ  AL  12522  MACEIO SHOP EXP   
1      Maxwell Vieira  JEFFERSON    LJ  AL  12817   SHOPPING PATIO   
2      Maxwell Vieira   VINICIUS    LJ  AL  12818      GB SERRARIA   
3      Maxwell Vieira   THAYLLAN    LJ  AL  12820         ATACADÃO   
4  Efigênia Herculano   MARCYARA    LJ  AL  12823      PONTA VERDE   

   PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO MARCA  \
0               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g  LILY   
1               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g  LILY   
2               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g  LILY   
3               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g  LILY   
4               89446  LILY CR AC DES HID CP LEAU/LILY SOL 200g  LILY   

             CATEGORIA  ...  C-4  C-3   C-2  C-1 VENDAS CICLO ATUAL  \
0  CUIDADOS COM A PELE  ...  0.0  2.0   2.0  0.0                0.0   
1  CUIDADOS COM A PELE  ...  8.0  1.0  24.0  1.0                0.0   
2  CUIDADOS COM A PELE  ...  0.0  2.0   7.0  1.0                0.0   
3  CUIDADOS COM A PELE  ...  4.0  1.0   1.0  1.0                0.0   
4  CUIDADOS COM A PELE  ...  1.0  0.0   0.0  2.0                0.0   

  PICO VENDAS SIMILAR ULTIMOS 6 CICLOS PV GINSENG  SUGESTÃO METASELLIN  \
0                                  2.0          2                        
1                                 24.0          4                        
2                                  7.0          1                        
3                                  4.0          2                        
4                                  2.0          1                        

  SUGESTÃO ABASTECIMENTO SUGESTÃO COMERCIAL  
0                                            
1                                            
2                                            
3                                            
4                                            

[5 rows x 31 columns]

In [119]:
df_final.columns

Index(['SUPERVISOR', 'ANALISTA', 'CANAL', 'UF', 'PDV', 'DESCRIÇÃO PDV',
       'PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'MARCA', 'CATEGORIA',
       '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'IAF', 'FOCO',
       'PRODUTO SIMILAR', 'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR',
       'VENDAS CICLO LANÇAMENTO', 'C-4', 'C-3', 'C-2', 'C-1',
       'VENDAS CICLO ATUAL', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
       'PV GINSENG', 'SUGESTÃO METASELLIN', 'SUGESTÃO ABASTECIMENTO',
       'SUGESTÃO COMERCIAL'],
      dtype='object')

In [120]:

# lista de colunas numéricas
numeric_cols = [
    'VENDAS CICLO LANÇAMENTO', 'C-4', 'C-3', 'C-2', 'C-1',
    'VENDAS CICLO ATUAL', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG', 'SUGESTÃO METASELLIN', 'SUGESTÃO ABASTECIMENTO',
    'SUGESTÃO COMERCIAL'
]

# colunas não numéricas = todas menos as numéricas
non_numeric_cols = [col for col in df_final.columns if col not in numeric_cols]

# agrupar por todas as não numéricas, pegando o máximo das numéricas
df_final_sem_dupli = (
    df_final
    .groupby(non_numeric_cols, as_index=False)[numeric_cols]
    .sum()
)


In [121]:
df_final_sem_dupli.head()

SUPERVISOR   ANALISTA CANAL   UF    PDV  DESCRIÇÃO PDV  PRODUTO LANÇAMENTO  \
0          0  JEFFERSON    LJ  BA3  24253  Matriz Centro               48780   
1          0  JEFFERSON    LJ  BA3  24253  Matriz Centro               49154   
2          0  JEFFERSON    LJ  BA3  24253  Matriz Centro               49193   
3          0  JEFFERSON    LJ  BA3  24253  Matriz Centro               49893   
4          0  JEFFERSON    LJ  BA3  24253  Matriz Centro               49943   

                   DESCRIÇÃO DO LANÇAMENTO         MARCA            CATEGORIA  \
0  COFFEE DES ANTIT AER WOMAN SEDUC 75g V4        COFFEE         DESODORANTES   
1   COFFEE DES COL UNIQ WOM FL/GOURM 100ml  CUIDE-SE BEM           PERFUMARIA   
2    COFFEE DES COL UNIQ MAN FOUG/OR 100ml        COFFEE           PERFUMARIA   
3    CBEM LOC DES HID CPO ROS/ALG V3 400ml      FLORATTA  CUIDADOS COM A PELE   
4  CBEM LOC DES HID CPO PESSEGURA V2 400ml  CUIDE-SE BEM  CUIDADOS COM A PELE   

   ...  C-4  C-3  C-2  C-1 VENDAS CICLO ATUAL  \
0  ...  1.0  0.0  2.0  2.0                0.0   
1  ...  1.0  0.0  0.0  1.0                0.0   
2  ...  0.0  1.0  0.0  1.0                0.0   
3  ...  4.0  2.0  2.0  1.0                1.0   
4  ...  2.0  1.0  1.0  1.0                0.0   

  PICO VENDAS SIMILAR ULTIMOS 6 CICLOS PV GINSENG  SUGESTÃO METASELLIN  \
0                                  2.0          0                        
1                                  1.0         28                        
2                                  1.0         28                        
3                                  4.0          2                        
4                                  2.0          0                        

  SUGESTÃO ABASTECIMENTO SUGESTÃO COMERCIAL  
0                                            
1                                            
2                                            
3                                            
4                                            

[5 rows x 31 columns]

In [122]:
df_final_sem_dupli.to_excel(f'C:/Users/joao.herculano/Documents/Lançamento{hoje}{ciclo_lanc}!!2.xlsx',index=False)